# Synchronization of ontology files
In this notebook we can look at the current state of the synchronization system between ontology files from a version control system and a wikibase instance.

## Setup

Setting up the Python path to import the module locally and starting the logging system.

In [1]:
import logging
import os
import sys

# set up module paths for imports
module_path = os.path.abspath(os.path.join('..'))
hercules_sync_path = os.path.abspath(os.path.join('..', 'hercules_sync'))
sys.path.append(module_path)
sys.path.append(hercules_sync_path)

# start logging system and set logging level
logger = logging.getLogger()
logger.setLevel(logging.INFO)
logging.info("Starting logger")

INFO:root:Starting logger


We can now start importing the dependencies from hercules_sync to execute the synchronization:
* The GitFile class encapsulates the diff of a file before and after changes have been made.
* We will use the GraphDiffSyncAlgorithm to obtain the differences from each ontology file. This algorithm parses the files into a graph and computes the difference between the original and the modified graph.
* The OntologySynchronizer class uses the algorithm to return the list of operations that need to be executed in the triplestore.

In [2]:
from hercules_sync.git import GitFile
from hercules_sync.synchronization import GraphDiffSyncAlgorithm, OntologySynchronizer

algorithm = GraphDiffSyncAlgorithm()
synchronizer = OntologySynchronizer(algorithm)

We are making use of a URIs factory mock to store the URIs of each entity from wikibase. Since we are starting from scratch in this example, we will reset its internal state:

In [ ]:
from hercules_sync.external.uri_factory_mock import URIFactory

factory = URIFactory()
factory.reset_factory()

Now we will create an instance of the WikibaseAdapter class to connect to our wikibase instance where the synchronization will be executed:

In [ ]:
from hercules_sync.triplestore import WikibaseAdapter
from secret import USERNAME, PASSWORD

mediawiki_api_url='https://unitest.wiki.opencura.com/w/api.php'
sparql_endpoint_url='http://unitest.wiki.opencura.com/query/sparql'

adapter = WikibaseAdapter(mediawiki_api_url, sparql_endpoint_url, USERNAME, PASSWORD)

Finally, we will create this helper function that executes the operations returned by the algorithm in the triplestore:

In [5]:
def execute_synchronization(source_content, target_content, synchronizer, adapter):
    gitfile = GitFile(None, source_content, target_content)
    ops = synchronizer.synchronize(gitfile)
    for op in ops:
        res = op.execute(adapter)
        if not res.successful:
            print(f"Error synchronizing triple: {res.message}")

## Adding content to the triplestore

In order to simulate the initial commit of an ontology file, we will start with an empty string as the source content, and the target content will represent the contents of the file after the commit:

In [6]:
source_content = ""

target_content = """
#################################################################
# Example ontology.                                             #
# This file is used to test the CI and synchronization systems. #
#################################################################

@prefix ex: <http://www.purl.org/hercules/asio/core#> .
@prefix owl: <http://www.w3.org/2002/07/owl#> .
@prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .

ex:AdministrativePersonnel rdf:type owl:Class ;
                           rdfs:subClassOf  ex:HumanResource ;
                           owl:disjointWith ex:ResearchPersonnel .

ex:HumanResource rdf:type owl:Class .

ex:ResearchPersonnel rdf:type owl:Class ;
                     rdfs:subClassOf ex:HumanResource .

ex:authors rdf:type owl:ObjectProperty .
"""

Before executing the synchronization, we are going to briefly inspect the operations created by the algorithm first:

In [7]:
gitfile = GitFile(None, source_content, target_content)
ops = synchronizer.synchronize(gitfile)

ops

In [8]:
str(ops[-1])

'AdditionOperation: URIElement: http://www.purl.org/hercules/asio/core#AdministrativePersonnel - Type: item - URIElement: http://www.w3.org/2002/07/owl#disjointWith - Type: item - URIElement: http://www.purl.org/hercules/asio/core#ResearchPersonnel - Type: item'

As we can see, we have 6 AdditionOperations to execute in the triplestore.
<br><br>

We can now execute the synchronization using the function defined in the setup section:

In [ ]:
execute_synchronization(source_content, target_content, synchronizer, adapter)

INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://www.purl.org/hercules/asio/core#AdministrativePersonnel - Type: item - URIElement: http://www.w3.org/2002/07/owl#disjointWith - Type: item - URIElement: http://www.purl.org/hercules/asio/core#ResearchPersonnel - Type: item
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://www.purl.org/hercules/asio/core#AdministrativePersonnel - Type: item - URIElement: http://www.w3.org/2000/01/rdf-schema#subClassOf - Type: item - URIElement: http://www.purl.org/hercules/asio/core#HumanResource - Type: item
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://www.purl.org/hercules/asio/core#authors - Type: property - URIElement: http://www.w3.org/1999/02/22-rdf-syntax-ns#type - Type: item - URIElement: http://www.w3.org/2002/07/owl#ObjectProperty - Type: item
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://www.purl.org/hercules

We can see below a sequence diagram of the complete process of adding new triples to the triplestore:

![abc](img/herc_sync_sequence_new_triple.png)

The process is equivalent to removing content from the triplestore, with the main difference that the 'remove_triple' method from WikibaseAdapter would be called instead.

## Modifying existing content

Now we are going to simulate a change in the ontology file previously created. The following changes are introduced:
* Add a new entity (ChangedPersonnel) of type owl:Class.
* Add labels and description to the ResearchPersonnel entity.
* Change the subclassOf property of ResearchPersonnel from HumanResource to ChangedPersonnel (for illustrative purposes).
* Change the disjointWith property of AdministrativePersonnel from ResearchPersonnel to ChangedPersonnel.
* Create a new 'authoredBy' property.
* Set 'authors' as a subProperty of 'authoredBy'.

In [10]:
source_content = target_content

target_content = """
#################################################################
# Example ontology.                                             #
# This file is used to test the CI and synchronization systems. #
#################################################################

@prefix ex: <http://www.purl.org/hercules/asio/core#> .
@prefix geo: <http://www.opengis.net/ont/geosparql#> .
@prefix owl: <http://www.w3.org/2002/07/owl#> .
@prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix asio: <http://www.asio.es/asioontologies/asio#> .
@prefix xsd: <http://www.w3.org/2001/XMLSchema#> .


ex:AdministrativePersonnel rdf:type owl:Class ;
                           rdfs:subClassOf  ex:HumanResource ;
                           owl:disjointWith ex:ChangedPersonnel .

ex:HumanResource rdf:type owl:Class .

ex:ChangedPersonnel rdf:type owl:Class .

ex:ResearchPersonnel rdf:type owl:Class ;
                        rdfs:subClassOf ex:ChangedPersonnel ;
                        rdfs:subClassOf ex:HumanResource ;
                        ex:creationDate "2019-12-31"^^xsd:date ;
                        rdfs:comment "Personnel devoted to technical suport."@en ;
                        rdfs:label "Personal tècnic"@ca ,
                                   "Personal técnico"@es ,
                                   "Personnel technique"@fr ,
                                   "Pessoal técnico"@pt ,
                                   "Technical personnel"@en .

ex:authoredBy rdf:type owl:ObjectProperty .

ex:authors rdf:type owl:ObjectProperty ;
           rdfs:subPropertyOf ex:authoredBy .

ex:location rdf:type owl:DatatypeProperty ;
            rdfs:range geo:wktLiteral .

ex:creationDate rdf:type owl:DatatypeProperty ;
                rdfs:range xsd:date .
"""

In [11]:
execute_synchronization(source_content, target_content, synchronizer, adapter)

## Removing content

Finally, we are going to remove some statements from our entities:
* Remove type statement from the ChangedPersonnel entity.
* Remove subclassOf statement from the ResearchPersonnel entity.
* Remove label @pt from ResearchPersonnel.
* Delete authors and authoredBy content.

In [12]:
source_content = target_content

target_content = """
#################################################################
# Example ontology.                                             #
# This file is used to test the CI and synchronization systems. #
#################################################################

@prefix ex: <http://www.purl.org/hercules/asio/core#> .
@prefix geo: <http://www.opengis.net/ont/geosparql#> .
@prefix owl: <http://www.w3.org/2002/07/owl#> .
@prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix asio: <http://www.asio.es/asioontologies/asio#> .
@prefix xsd: <http://www.w3.org/2001/XMLSchema#> .


ex:AdministrativePersonnel rdf:type owl:Class ;
                           rdfs:subClassOf  ex:HumanResource ;
                           owl:disjointWith ex:ChangedPersonnel .

ex:HumanResource rdf:type owl:Class .

ex:ResearchPersonnel rdf:type owl:Class ;
                        rdfs:comment "Personnel devoted to technical suport."@en ;
                        rdfs:label "Personal tècnic"@ca ,
                                   "Personal técnico"@es ,
                                   "Personnel technique"@fr ,
                                   "Technical personnel"@en .
"""

In [13]:
execute_synchronization(source_content, target_content, synchronizer, adapter)

# Testing synchronization of current ontology 

In [6]:
import requests

source_content = ""

target_content = requests.get('http://www.weso.es/hercules-ontology/asio.ttl').text

In [ ]:
execute_synchronization(source_content, target_content, synchronizer, adapter)

INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_DIVISION_LEVEL_1_FIPS_CODE_SP07 - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#inScheme - Type: item - URIElement: http://purl.org/hercules/asio/modules#ESRegionFIPSCodeList - Type: item
/Users/alejandro/anaconda3/envs/weso/lib/python3.7/site-packages/wikidataintegrator/wdi_core.py:218: UserWarning: Warning: No distinct value properties found
Please set P2302 and Q21502410 in your wikibase or set `core_props` manually.
Continuing with no core_props
  "Please set P2302 and Q21502410 in your wikibase or set `core_props` manually.\n" +
/Users/alejandro/anaconda3/envs/weso/lib/python3.7/site-packages/wikidataintegrator/wdi_core.py:175: UserWarning: mapping relation types are being ignored
  warnings.warn("mapping relation types are being ignored")
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#E

Error while writing to Wikidata
Error synchronizing triple: The supplied language code was not recognized.


INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/core#MastersDegree - Type: item - URIElement: http://www.w3.org/2000/01/rdf-schema#label - Type: item - LiteralElement: Maîtrise universitaire - Language: fr-ca
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_SUBJECT_AREA_LEVEL_3_TRA - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#prefLabel - Type: property - LiteralElement: Tresporte - Language: ast


Error while writing to Wikidata
Error synchronizing triple: The supplied language code was not recognized.


INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_DIVISION_LEVEL_1_INEES_CODE_15 - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#inScheme - Type: item - URIElement: http://purl.org/hercules/asio/modules#ESRegionINEESCodeList - Type: item
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_SCIENTIFIC_DOMAIN_LEVEL_2_QMC - Type: item - URIElement: http://www.w3.org/2000/01/rdf-schema#label - Type: item - LiteralElement: Química
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_UNIVERSITY_ERASMUS_CODE_E_GRANADA01 - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#inScheme - Type: item - URIElement: http://purl.org/hercules/asio/modules#ESUniversityErasmusCodeList - Type: item
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercu

...

INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_SCIENTIFIC_DOMAIN_LEVEL_3_CODE_FFIVVJH - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#inScheme - Type: item - URIElement: http://purl.org/hercules/asio/modules#ESscientificDomains3rdCodeList - Type: item
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_UNIVERSITY_013 - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#prefLabel - Type: property - LiteralElement: Universitat d'Oviedo - Language: ca
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_UNIVERSITY_002 - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#prefLabel - Type: property - LiteralElement: Universitat d'Extremadura - Language: ca
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modu

Error while writing to Wikidata
Error synchronizing triple: The supplied language code was not recognized.


INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_DIVISION_LEVEL_1_ES_RI - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#prefLabel - Type: property - LiteralElement: La Rioja - Language: oc
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_DIVISION_LEVEL_2_ISO_CODE_ES_SS - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#inScheme - Type: item - URIElement: http://purl.org/hercules/asio/modules#ESProvinceISOCodeList - Type: item
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_UNIVERSITY_030 - Type: item - URIElement: http://purl.org/hercules/asio/core#hasCode - Type: property - URIElement: http://purl.org/hercules/asio/modules#ES_UNIVERSITY_VAT_NUMBER_R4868004E - Type: item
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/

Error while writing to Wikidata
Error synchronizing triple: The requested feature is not supported by the given entity.


INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_SCIENTIFIC_DOMAIN_LEVEL_3_PSFRSQ - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#prefLabel - Type: property - LiteralElement: Psicobiologia - Language: pt
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/core#utilizes - Type: property - URIElement: http://www.w3.org/2000/01/rdf-schema#range - Type: item - URIElement: http://purl.org/hercules/asio/core#ResearchMaterial - Type: item
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_SUBJECT_AREA_LEVEL_3_CODE_PS3 - Type: item - URIElement: http://www.w3.org/1999/02/22-rdf-syntax-ns#type - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#Concept - Type: item
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/core#DoctoralDegree

# Instances test

In [8]:
source_content = ""

with open('tmp.ttl', 'r') as f:
    target_content = f.read()

In [9]:
execute_synchronization(source_content, target_content, synchronizer, adapter)

INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_SUBJECT_AREA_LEVEL_3_CODE_FFP - Type: item - URIElement: http://www.w3.org/2000/01/rdf-schema#label - Type: item - LiteralElement: FFP
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_SUBJECT_AREA_LEVEL_3_CODE_ALI - Type: item - URIElement: http://www.w3.org/1999/02/22-rdf-syntax-ns#type - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#Concept - Type: item
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ScientificDomain - Type: item - URIElement: http://www.w3.org/1999/02/22-rdf-syntax-ns#type - Type: item - URIElement: http://www.w3.org/2002/07/owl#Class - Type: item
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/core#NationalProject - Type: item - URIElement: http://www

Error while writing to Wikidata
Error synchronizing triple: "es-ES" is not a known language code.


INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_SUBJECT_AREA_LEVEL_1_CMIFQ - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#prefLabel - Type: property - LiteralElement: Ciències matemàtiques, físiques, químiques i enginyeries - Language: ca
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://www.asio.es/asioinstances/asio#WESO - Type: item - URIElement: http://xmlns.com/foaf/0.1/member - Type: property - URIElement: http://www.asio.es/asioinstances/asio#GuillermoFacundoColunga - Type: item
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_SCIENTIFIC_DOMAIN_LEVEL_2_FI - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#prefLabel - Type: property - LiteralElement: Physics and space sciences - Language: en
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercule

Error while writing to Wikidata
Error synchronizing triple: The supplied language code was not recognized.


INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_SCIENTIFIC_DOMAIN_LEVEL_1_CODE_CSH - Type: item - URIElement: http://www.w3.org/2000/01/rdf-schema#label - Type: item - LiteralElement: CSH
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/core# - Type: item - URIElement: http://purl.org/dc/terms/license - Type: property - URIElement: https://creativecommons.org/publicdomain/zero/1.0/ - Type: item
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_SUBJECT_AREA_LEVEL_3_AYA - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#prefLabel - Type: property - LiteralElement: Astronomy and astrophysics - Language: en
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://www.asio.es/asioinstances/asio#UniversityOfOviedoSchoolOfComputerScienceEngineering - Type: item - URIEle

...

INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/core#publicationDate - Type: property - URIElement: http://www.w3.org/2000/01/rdf-schema#range - Type: item - URIElement: http://www.w3.org/2001/XMLSchema#date - Type: item
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/core#MastersThesis - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#prefLabel - Type: property - LiteralElement: Tese de mestrado - Language: pt-ao
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_SUBJECT_AREA_LEVEL_2_BME - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#prefLabel - Type: property - LiteralElement: Biomedicina  - Language: es


Error while writing to Wikidata
Error synchronizing triple: The supplied language code was not recognized.


INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_SUBJECT_AREA_LEVEL_3_MTM - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#prefLabel - Type: property - LiteralElement: Ciencias matemáticas - Language: es
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/modules#ES_SCIENTIFIC_DOMAIN_LEVEL_3_CODE_CTFIST - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#prefLabel - Type: property - LiteralElement: CTFIST
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://purl.org/hercules/asio/core#AcademicDegree - Type: item - URIElement: http://www.w3.org/2004/02/skos/core#prefLabel - Type: property - LiteralElement: Grau académico - Language: pt-pt
INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://www.asio.es/asioinstances/asio#BasqueCentreForClimateChange - Type: item - URIElement: http://purl

Error while writing to Wikidata
Error synchronizing triple: The supplied language code was not recognized.


INFO:hercules_sync.triplestore.wikibase_adapter:Create triple: URIElement: http://www.asio.es/asioinstances/asio#GravitySupergravitySuperstrings - Type: item - URIElement: http://purl.org/hercules/asio/core#projectStartDate - Type: property - LiteralElement: 2010-01-01 - DataType: http://www.w3.org/2001/XMLSchema#date


## Future work

For additional information about the work that needs to be done with the synchronization system, please visit: https://github.com/weso/hercules-sync/issues?q=is%3Aopen+is%3Aissue+label%3Awikibase+